# 羽毛球3D轨迹可视化（示例与说明）
本Notebook演示如何加载数据、绘制标准3D羽毛球场地、可视化多条轨迹，并播放动画。

In [1]:
!pip -q install plotly pandas numpy 'nbformat>=4.2.0'


[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python3 -m pip install --upgrade pip


## 1. 导入与依赖

In [2]:
from pathlib import Path
import json
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import sys
from itertools import chain
# sys.path.append(str(Path('.').resolve()))
# sys.path.append('./')
from badminton_vis import (
    CourtSpec, load_from_json_file,
    sort_and_clean, smooth, interpolate_time, make_figure, make_animation,
    save_html, make_parabola_example
)

## 2. 数据格式与示例
示例JSON位于 `/mnt/data/badminton_3d_vis/sample_trajectory.json`，符合规格中的字段定义。

In [3]:
pred_track_path = './pred_track.json'
with open(pred_track_path, 'r', encoding='utf-8') as f:
    pred_obj = json.load(f)

pred_obj


{'msgtype': 'pred_track',
 'pid': '8bcf3e49',
 'positions': [{'frame_id': 3797,
   'left': {'x': 948.0, 'y': 596.0},
   'pos': {'x': 785.5364990234375,
    'y': -0.6191643476486206,
    'z': 132.67044067382812},
   'right': {'x': 928.0, 'y': 601.0},
   'ts': 1756453901741.691,
   'type': 'node',
   'vx': 0.0,
   'vy': 0.0,
   'vz': 0.0},
  {'frame_id': 3798,
   'left': {'x': 953.0, 'y': 586.0},
   'pos': {'x': 776.708740234375,
    'y': -3.0229578018188477,
    'z': 139.25697326660156},
   'right': {'x': 930.0, 'y': 591.0},
   'ts': 1756453901747.963,
   'type': 'node',
   'vx': 0.0,
   'vy': 0.0,
   'vz': 0.0},
  {'frame_id': 3799,
   'left': {'x': 961.0, 'y': 571.0},
   'pos': {'x': 762.2846069335938,
    'y': -6.725035667419434,
    'z': 148.83717346191406},
   'right': {'x': 933.0, 'y': 576.0},
   'ts': 1756453901760.494,
   'type': 'node',
   'vx': 0.0,
   'vy': 0.0,
   'vz': 0.0},
  {'frame_id': 3800,
   'left': {'x': 966.0, 'y': 561.0},
   'pos': {'x': 762.4082641601562,
    'y'

In [4]:
track_alls_path = './track_alls.json'
with open(track_alls_path, 'r', encoding='utf-8') as f:
    track_alls_obj = json.load(f)
track_alls_obj

[{'msgtype': 'pred_track',
  'pid': '8bcf3e49',
  'positions': [{'frame_id': 3797,
    'left': {'x': 948.0, 'y': 596.0},
    'pos': {'x': 785.5364990234375,
     'y': -0.6191643476486206,
     'z': 132.67044067382812},
    'right': {'x': 928.0, 'y': 601.0},
    'ts': 1756453901741.691,
    'type': 'node',
    'vx': 0.0,
    'vy': 0.0,
    'vz': 0.0},
   {'frame_id': 3798,
    'left': {'x': 953.0, 'y': 586.0},
    'pos': {'x': 776.708740234375,
     'y': -3.0229578018188477,
     'z': 139.25697326660156},
    'right': {'x': 930.0, 'y': 591.0},
    'ts': 1756453901747.963,
    'type': 'node',
    'vx': 0.0,
    'vy': 0.0,
    'vz': 0.0},
   {'frame_id': 3799,
    'left': {'x': 961.0, 'y': 571.0},
    'pos': {'x': 762.2846069335938,
     'y': -6.725035667419434,
     'z': 148.83717346191406},
    'right': {'x': 933.0, 'y': 576.0},
    'ts': 1756453901760.494,
    'type': 'node',
    'vx': 0.0,
    'vy': 0.0,
    'vz': 0.0},
   {'frame_id': 3800,
    'left': {'x': 966.0, 'y': 561.0},
    '

## 3. 加载与解析
支持从JSON对象/文件或DataFrame加载，自动生成 `pid, frame_id, ts, x, y, z, vx, vy, vz` 字段。

In [5]:
# pred_trajs = load_from_json_file(pred_track_path)
# real_trajs = load_from_json_file(real_track_path)
track_alls_trajs = load_from_json_file(track_alls_path)  # 新增：加载多条抛物线
all_trajs = list(chain(track_alls_trajs))  # 合并所有轨迹
df = pd.concat([t.to_dataframe() for t in all_trajs], ignore_index=True)
df = sort_and_clean(df)
df.head()

pid  track_id  frame_id  type            ts           x         y  \
0  8bcf3e49        98      3797  node  1.756454e+12  785.536499 -0.619164   
1  8bcf3e49        98      3797  node  1.756454e+12  785.536499 -0.619164   
2  8bcf3e49        98      3798  node  1.756454e+12  776.708740 -3.022958   
3  8bcf3e49        98      3798  node  1.756454e+12  776.708740 -3.022958   
4  8bcf3e49        98      3799  node  1.756454e+12  762.284607 -6.725036   

            z   vx   vy   vz  
0  132.670441  0.0  0.0  0.0  
1  132.670441  0.0  0.0  0.0  
2  139.256973  0.0  0.0  0.0  
3  139.256973  0.0  0.0  0.0  
4  148.837173  0.0  0.0  0.0

## 4. 绘制静态3D场地与轨迹

In [6]:
court = CourtSpec()  # 可传入自定义尺寸
fig = make_figure(df, court=court, title='Badminton 3D Trajectories - Static')
fig.show()


## 5. 轨迹动画（根据时间戳ts）

In [7]:
anim_fig = make_animation(df, court=CourtSpec(), title='Badminton 3D Trajectory Animation', time_col='ts')
anim_fig.show()


## 6. 多轨迹演示与平滑/插值
这里创建另一条仿真轨迹并与示例轨迹一起显示，同时展示平滑与按固定时间步长插值。

In [8]:
# 生成另一条抛物线轨迹
demo_trajs = make_parabola_example(pid='50651a30', apex=(0.0, -1.0, 6.0), span_x=7.0)
df2 = pd.concat([t.to_dataframe() for t in demo_trajs], ignore_index=True)
df_multi = pd.concat([df, df2], ignore_index=True)
df_multi = sort_and_clean(df_multi)

# 可选：平滑
df_smooth = smooth(df_multi, window=5)

# 可选：按固定时间步插值（需要ts列）
df_interp = interpolate_time(df_smooth, freq_ms=20)

fig_multi = make_figure(df_interp, court=CourtSpec(), title='Multiple Trajectories (Smoothed & Interpolated)')
fig_multi.show()


TypeError: Trajectory.__init__() missing 2 required positional arguments: 'track_id' and 'msgtype'

## 7. 导出（HTML）

In [ ]:
export_path = '/mnt/data/badminton_3d_vis/trajectory_visualization.html'
save_html(fig_multi, export_path)
export_path


## 8. 常见问题（FAQ）
- **坐标单位**：默认以米为单位。
- **坐标系**：原点在场地中心地面，x为场地长度方向，y为宽度方向，z向上。
- **自定义场地**：通过 `CourtSpec(length=..., width_doubles=..., net_height_center=...)` 调整。
- **数据来源**：可使用 `load_from_json_file/json_obj/dataframe` 加载；DataFrame方式可映射自定义列名。
- **动画时间**：优先使用 `ts`（毫秒）；如缺失，将按采样序号合成时间。
- **导出**：使用 `save_html(fig, path)` 导出可交互HTML，便于分享。